Dear User,

This is a tutorial script showcasing the testing modules of the IonoBench Framework. It also serves as an introductory documentation script for the framework for you to download datasets and trained models.

**Instructions** 

You can download the provided dataset and pretrained models, then run the test modules to replicate paper results.

This notebook is designed to run on **local machines** using tools like **VS Code (interactive Python), Jupyter Notebook, or JupyterLab**.  
Make sure your system has a compatible **GPU environment** set up with PyTorch and CUDA.  
To verify that GPU is working correctly, see section `# 0: Preps >>> Verify GPU session`.

Please run the notebook **step-by-step**, following the comments provided.

There are three main testing sections:
- **3b. Default Test**  
- **4a. Solar Analysis**  
- **4b. Storm Analysis**

Both the default test and solar analysis are commented out for your convenience, as each may take ~20 minutes to run. If you prefer a quicker test, you can leave them commented and run the **Storm Analysis** section, which completes in a few minutes.

After that section you can observe the paper results on `5.3.3. Visual Comparison: Residual Patterns during Stormy vs. Quiet Conditions` (Specifically first two rows: stormy example.)  
If you wait for other test runs you can reproduce the paper results in `5.1. Overall Performance` and `5.2. Performance Across Solar Activity Levels`.

Start with the default model “SimVPv2.”  
If you want to **test other models**, just restart the notebook. Make sure you:
- Download the new model weights from `2: Models and Configs` and change the path in `3a: Loading Pre-trained Model`.
- Change the model name in the configs.
- Give each run a unique session name so the results are stored separately before you start the test parts.

**Common Issues You Might Face:**
- **CUDA not available:** Ensure your GPU environment is correctly configured and CUDA is available to PyTorch.
- **Interrupted downloads:** If dataset or model download fails due to interruption, delete any existing `datasets/` or `training_sessions/` folders and try again.
- **File/path issues:** Ensure relative paths in the configs match your local directory structure.

**Note: All repeating cells used for data preparation before different testing types will be hidden using CLI support. Currently this notebook is showing how the underlying config structure and functions work.**


--- 
## 0: Preps  
Clone repo, install requirements, and verify GPU


In [1]:
# 0: Preps >>> Verify GPU session
#================================================================
import torch
print("CUDA available:", torch.cuda.is_available())
print("Device name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "No GPU")
print(f'CUDA version: {torch.version.cuda}')
#================================================================

CUDA available: True
Device name: NVIDIA RTX A5000
CUDA version: 12.4


Please don't continue if `CUDA available: False` and select GPU again and restart session.

--- 
#### Colab Preps (Skip if local build)

--- 
## 1: Dataset  


If chronological split is desired, change to "chronological" However for chronological you can only replicate the Paper Results on  `Section 4 Investigating Future Bias in Stratified Split `

In [2]:
# 1: Dataset >>> Download the desired IonoBench dataset (Stratified or Chronological split)
#==================================================================================
from pathlib import Path
import sys

base_path = Path.cwd().parent
sys.path.append(str(base_path))
sys.path.append('./source')
sys.path.append('./scripts')
from source.myDataFuns import download_dataset
download_dataset(
    dataset_name="stratified",  # If chronological split is desired, change to "chronological" However for chronological you can only replicate the Paper Results on Section 4
    base_path=base_path
    )     
#==================================================================================


IonoBench_stratifiedSplit.pickle already exists. Skipping.
OMNI_data_1996to2024.txt already exists. Skipping.


In [3]:
# 1: Dataset >>> Read dataset
#====================================================================================
from scripts.data import load_training_data

dataDict = load_training_data(
                            seq_len=12,                
                            pred_horz=12,
                            datasplit='stratified',      # Need to be changed according to the datasplit
                            features = None,             # Default "None" loads all features, otherwise specify a list of features i.e ['F10.7', 'Dst']
                            base_path=base_path
                            )        
# You can also see the full list of features in ~/configs/base.yaml

print("\n", "-" * 20, "\n", dataDict.keys())
print("You can use the dataDict following dict_keys as you like from this point on.")
#====================================================================================

--------------------
Base Path: /usr1/home/s124mdg45_01/IonoBench
Function Path: /usr1/home/s124mdg45_01/IonoBench/source
Training Data Path: /usr1/home/s124mdg45_01/IonoBench/datasets
--------------------
Training data loaded successfully.
--------------------
Important Details:
Data Range: 2000-01-01 00:00:00 - 2024-09-11 20:00:00
Shapes=> Dates: 108251, TEC: (108251, 72, 72), OMNI: (108251, 17)
Data Split Sets: ['train_v1', 'test_v1', 'train_v2', 'valid_v1', 'train_v3', 'test_v2', 'train_v4', 'valid_v2', 'train_v5', 'test_v3', 'train_v6', 'valid_v3']
Storm Info: ['Intense', 'Superintense']
Max TEC: 210.100, Min TEC: 0.0
--------------------
Train: 74880, Valid: 16597, Test: 16344
Dataset Name: stratified 
 Ratio => Train: 0.69, Valid: 0.15, Test: 0.15

 -------------------- 
 dict_keys(['dates', 'normTEC', 'normOMNI', 'OMNI_names', 'dataSplit_Dates', 'stormInfo', 'maxTEC', 'minTEC', 'NUM_OMNI', 'base_path', 'training_data_path', 'script_dir'])
You can use the dataDict following dict

In [4]:
# 1: Dataset >>> Ex: Accessing specific OMNI features
#====================================================================================
dataDict['OMNI_names']
#=====================================================================================

['F10.7',
 'Dst',
 'ap',
 'AE',
 'pc',
 'SW Temp',
 'SW Density',
 'SW Speed',
 'SW Long Angle',
 'SW Lat Angle',
 'Flow Pressure',
 'E Field',
 'Scalar B',
 'BZ (GSM)',
 'Year',
 'Day of Year',
 'Hour']

In [5]:
# 1: Dataset >>> Ex: Accessing specific OMNI features (note: all features are normalized to 0-1) 
#=====================================================================================
'''
"normOMNI" is same order with the "OMNI_names"
Check the name and access the desired feature using the getOMNIfeature function.
'''
from source.myDataFuns import getOMNIfeature

# To access 'Dst' values 
print("Dst:", getOMNIfeature(dataDict,"Dst")) # Dst values
print("Year:", getOMNIfeature(dataDict,"Year")) # Year values

#======================================================================================

Dst: [0.7555110220440882 0.7715430861723446 0.7555110220440882 ...
 0.9158316633266532 0.8897795591182364 0.8857715430861722]
Year: [0.0 0.0 0.0 ... 1.0 1.0 1.0]


In [6]:
# 1: Dataset >>> Ex: Accessing TEC data for specific date range (note: tec data is normalized to 0-1)
#======================================================================================
from datetime import datetime, timedelta
from source.myDataFuns import dateList
# Select the date period
startDate = datetime(2024, 5, 9, 0, 0)  # Start date
endDate = datetime(2024, 5, 9, 22, 0)    # End date (inclusive)

# Find idx corresponding to start and end dates
startidx = dataDict['dates'].index(startDate)
endidx = dataDict['dates'].index(endDate)

# Extract TEC data for the selected date range
norm_tecData = dataDict['normTEC'][startidx:endidx+1]
date_list = dateList(startDate, endDate,timedelta(hours=2)) # TEC maps are 2 hours apart
print("TEC data shape for the selected date range:", norm_tecData.shape)
print("Dates of the selected date range:", len(date_list))
#======================================================================================

TEC data shape for the selected date range: (12, 72, 72)
Dates of the selected date range: 12


In [7]:
# 1: Dataset >>> Reversing the Preprocessing Steps and Visualizing the Original TEC Data
#======================================================================================
'''
To recover original TEC data, the preprocessing steps (Normalization and heliocentric transformation) needs to be reversed.
Below is a demonstration of how to reverse the preprocessing steps and visualize the original TEC data. 
'''
from source.myDataFuns import reverseHeliocentric
tecData = norm_tecData*(dataDict['maxTEC'] - dataDict['minTEC']) + dataDict['minTEC']  # Reverse normalization
org_tecData = reverseHeliocentric(tecData, date_list)

from source.myVisualFuns import makeComparison_Anim
from IPython.display import HTML
# Define the plot titles for the animation
plot_titles = {
    'main': 'Reverse Heliocentric Transformation',
    'subplot1': 'Real VTEC IGS',
    'subplot2': 'Longitude-Shifted VTEC IGS',
    'colorbar': 'TECU (10$^{16}$ e/m$^2$)'
}

# Create a comparison animation of the original and transformed TEC data
'''
This is for demonstration purposes. Reversing the effect of the heliocentric transformation is shown in below animation
Right side shows after reverse heliocentric transformation, left side shows dataset TEC data before transformation.
'''
anim = makeComparison_Anim(
    data1=org_tecData,
    data2=tecData,
    date_list=date_list,
    titles=plot_titles,
    show_metrics=False,
    save=True,
    save_dir=base_path / "visuals",
)
HTML(anim.to_jshtml())  
#======================================================================================

Saving → /usr1/home/s124mdg45_01/IonoBench/visuals/Reverse_Heliocentric_Transformation_20240509_0000.gif


--- 
## 2: Models  

In [17]:
# 2: Models and Configs >>> Download the desired Trained Model (SimVP2,SwinLSTM, DCNN etc.) from Hugging Face Hub
#==================================================================================
from pathlib import Path

from source.myDataFuns import download_model_folder

data_path = Path(base_path, "training_sessions")         # ..~/IonoBench/training_sessions 
data_path.mkdir(parents=True, exist_ok=True)             # Create new folder when model folder is downloaded.

                          #
download_model_folder(                                   # This function automatically downloads the paper's model folder from Hugging Face Hub.
                    model_name = "DCNN",              # Change to "DCNN", "SwinLSTM", "SimVPv2_Chrono" for other models.
                    base_path = base_path
                    )    
#==================================================================================


DCNN_in12_out12_best_checkpoint_20250410_0940.pth already exists. Skipping.
DCNN_in12_out12_lr0.0001_bs32_20250410_0940.txt already exists. Skipping.
testing_info_2025-06-07_18-00-01.txt already exists. Skipping.
Please check the /usr1/home/s124mdg45_01/IonoBench/training_sessions/DCNN folder for the downloaded files.


In [18]:
# 2: Models and Configs >>> Load the model configurations
#==================================================================================
from scripts.loadConfigs import load_configs

'''
Configs uses base => model => mode => CLI override hierarchy.
You can change the model and mode to load different configurations.
For example, change "SimVPv2" to "DCNN121", "SwinLSTM" etc. to load different model configurations.
load_configs will return a merged configurations of the base, model, and mode.
'''

cfgs = load_configs(
                 model = "SimVPv2",  # Change to "DCNN121", "SwinLSTM", "SimVPv2_Chrono" for other models.
                 mode = "test",         
                 split = "stratified",  
                 base_path= base_path
                 )
#==================================================================================

In [19]:
# 2: Models and Configs >>> Can check the keys of the config dictionary
#================================================================
print(cfgs.keys())
print(cfgs.data.keys())
print(cfgs.model.keys())
print(cfgs.data.data_split)
print(cfgs.model)
#================================================================

dict_keys(['session', 'paths', 'defaults', 'data', 'train', 'test', 'model', 'mode'])
dict_keys(['seq_len', 'pred_horz', 'batch_size', 'shuffle', 'data_split', 'features'])
dict_keys(['name', 'input_shape', 'hid_S', 'hid_T', 'N_S', 'N_T', 'model_type', 'mlp_ratio', 'drop', 'drop_path', 'spatio_kernel_enc', 'spatio_kernel_dec', 'conv_in_channels', 'conv_out_channels', 'conv_kernel_size', 'conv_stride'])
stratified
{'name': 'SimVPv2', 'input_shape': [12, 18, 72, 72], 'hid_S': 16, 'hid_T': 256, 'N_S': 4, 'N_T': 4, 'model_type': 'gSTA', 'mlp_ratio': 8.0, 'drop': 0.0, 'drop_path': 0.0, 'spatio_kernel_enc': 3, 'spatio_kernel_dec': 3, 'conv_in_channels': 18, 'conv_out_channels': 1, 'conv_kernel_size': [1, 1, 1], 'conv_stride': [1, 1, 1]}


--- 
## 3: Testing Trained Models 
--- 


### 3a: Loading Pre-trained Model


In [20]:
# 3a: Loading Pre-trained Model>>> Prepare the data and build the model     
#=================================================================

from scripts.registry import build_model
from scripts.data import prepare_raw

# Prepare the data for testing
data = prepare_raw(cfgs)               # This fun Wraps load_training_data & patches cfg with shape/min-max info.
B = cfgs.test.batch_size               # batch size from YAML
T = cfgs.data.seq_len                  # input sequence length
C = cfgs.data.num_omni + 1             # OMNI scalars + TEC map channel
H = cfgs.data.H                        # height (set inside prepare_raw)
W = cfgs.data.W                        # width  (set inside prepare_raw)
cfgs.test.input_names = data['OMNI_names']          # This sets the input names for test logging file


device = "cuda:0" if torch.cuda.is_available() else "cpu"  # Use GPU if available, otherwise CPU
# Build the model
cfgs.model.input_shape = (T, C, H, W)  # Set input shape for the model
model = build_model(cfg = cfgs, base_path=base_path, device=device)           # Build the model with the configurations
print(f"Batch size: {B}, T: {T}, C: {C}, H: {H}, W: {W}")
#==================================================================

--------------------
Base Path: /usr1/home/s124mdg45_01/IonoBench
Function Path: /usr1/home/s124mdg45_01/IonoBench/source
Training Data Path: /usr1/home/s124mdg45_01/IonoBench/datasets
--------------------
Training data loaded successfully.
--------------------
Important Details:
Data Range: 2000-01-01 00:00:00 - 2024-09-11 20:00:00
Shapes=> Dates: 108251, TEC: (108251, 72, 72), OMNI: (108251, 17)
Data Split Sets: ['train_v1', 'test_v1', 'train_v2', 'valid_v1', 'train_v3', 'test_v2', 'train_v4', 'valid_v2', 'train_v5', 'test_v3', 'train_v6', 'valid_v3']
Storm Info: ['Intense', 'Superintense']
Max TEC: 210.100, Min TEC: 0.0
--------------------
Train: 74880, Valid: 16597, Test: 16344
Dataset Name: stratified 
 Ratio => Train: 0.69, Valid: 0.15, Test: 0.15
Batch size: 128, T: 12, C: 18, H: 72, W: 72


In [21]:
# 3a: Loading Pre-trained Model >>> Summary of the model   
#=================================================================
from torchinfo import summary
summary(model, input_size=((B, C, T, H, W),(B, cfgs.data.pred_horz, H, W)))
#=================================================================

Layer (type:depth-idx)                                  Output Shape              Param #
SimVPv2_Model                                           [128, 12, 72, 72]         --
├─Encoder: 1-1                                          [1536, 16, 18, 18]        --
│    └─Sequential: 2-1                                  --                        --
│    │    └─ConvSC: 3-1                                 [1536, 16, 72, 72]        2,640
│    │    └─ConvSC: 3-2                                 [1536, 16, 36, 36]        2,352
│    │    └─ConvSC: 3-3                                 [1536, 16, 36, 36]        2,352
│    │    └─ConvSC: 3-4                                 [1536, 16, 18, 18]        2,352
├─MidMetaNet: 1-2                                       [128, 12, 16, 18, 18]     --
│    └─Sequential: 2-2                                  --                        --
│    │    └─MetaBlock: 3-5                              [128, 256, 18, 18]        820,288
│    │    └─MetaBlock: 3-6                 


!!!! **Before loading the weights to build model**  Change the Path of **torch.load** to the path of your downloaded model checkpoint folder if you are trying DCNN or SwinLSTM. (Default is set to SimVPv2)
You can find the checkpoint file in the downloaded model folder under `training_sessions/{modelName}` as .... `"NameofTheSession"_best_checkpoint_"yyyymmdd"_"hhmm" `
To download new pre-trained model, refer back to the `2: Models and Configs >>> Download the desired Trained Model` section.


In [22]:
# 3a: Loading Pre-trained Model >>> Load the model weights from a checkpoint file
#====================================================================================
from source.myTrainFuns import DDPtoSingleGPU
import torch

checkpoint = torch.load(
    r'/usr1/home/s124mdg45_01/IonoBench/training_sessions/SimVPv2/SimVP_stratifiedSplit_Allfeatures_best_checkpoint_20250320_1401.pth',            # <= Copy inside
    weights_only=True)
model.load_state_dict(DDPtoSingleGPU(checkpoint["model_state_dict"]))   # Load the model state dict If DDP(Multiple GPU) was used get rid of Module prefix
#====================================================================================

<All keys matched successfully>

--- 
### 3b: Default Test

---

**!!! Disclaimer !!!**  
The paper’s experiments were primarily trained and tested using **4 GPUs with Distributed Data Parallel (DDP)**.  
DDP introduces some non-determinism, even with fixed random seeds, due to differences in data shuffling and the order of floating-point operations across GPUs.

This notebook uses a **single GPU**, which may lead to minor variations between the metrics generated here and those reported in the paper

These differences are **statistically negligible** and can be validated by comparing with the reported results.  
The key point is that these differences will not affect the paper's overall findings or the relative performance ranking of the models.

For bit-for-bit reproducibility of your own experiments, it is essential to use a fixed hardware configuration (e.g., the same number of GPUs) for both training and evaluation.

---

In [23]:
# 3b: Default Test >>> Setup the data loaders for testing
#================================================================
from scripts.data import make_default_loaders
loaders = make_default_loaders(cfg = cfgs, d = data)                # Make default loaders for training, validation, and test sets.
len(loaders["train"]), len(loaders["valid"]), len(loaders["test"])
#================================================================

(585, 130, 128)

In [24]:
# 3b: Default Test >>> Test the model (Default: test set) (RUN TIME: >~20 min)
#================================================================
from source.myTrainFuns import IonoTester

# FOR DEFAULT TESTING UNCOMMENT BELOW
#================================================================
'''
cfgs.test.save_results = True           # Save the test results to a log file (txt).
cfgs.test.save_raw = False              # Save the raw test results (Prediction Dates, TEC predictions and dedicated truth maps) to npz.
cfgs.session.name = "SimVPv2_test"      # Write a session name for the test results. New name will create a new folder in the ~/IonoBenchv1/training_sessions/
testDict = IonoTester(model, loaders['test'], device=device, config=cfgs).test() 
'''
#====================================================================================

'\ncfgs.test.save_results = True           # Save the test results to a log file (txt).\ncfgs.test.save_raw = False              # Save the raw test results (Prediction Dates, TEC predictions and dedicated truth maps) to npz.\ncfgs.session.name = "SimVPv2_test"      # Write a session name for the test results. New name will create a new folder in the ~/IonoBenchv1/training_sessions/\ntestDict = IonoTester(model, loaders[\'test\'], device=device, config=cfgs).test() \n'

--- 
## 4: Solar and Storm Analysis
---
  


### 4a: Solar Analysis

In [25]:
# 4a: Solar and Storm Analysis >>> Solar Loaders 
#====================================================================================
from scripts.data import make_solar_loaders

if "loaders" in locals():
    del loaders, data, cfgs             # To clear memory before loading solar loaders
    
import gc
gc.collect()
torch.cuda.empty_cache()

cfgs = load_configs(
                 model = "SimVPv2",  # <= change to "DCNN121", "SwinLSTM" for other models. (But the loaded model should match the model name)
                 mode = "solar",     # <= The testing type is set to "solar" to load solar configurations dynmaically.
                 split = "stratified",  
                 base_path= base_path
                 )
cfgs.paths.base_dir = base_path
data = prepare_raw(cfgs)                # Prepare the data (again neeeded for setting important parameters to config inside) 
loaders = make_solar_loaders(cfg = cfgs, base_path=base_path, d = data)                # Make default loaders for training, validation, and test sets.
#====================================================================================

--------------------
Base Path: /usr1/home/s124mdg45_01/IonoBench
Function Path: /usr1/home/s124mdg45_01/IonoBench/source
Training Data Path: /usr1/home/s124mdg45_01/IonoBench/datasets
--------------------
Training data loaded successfully.
--------------------
Important Details:
Data Range: 2000-01-01 00:00:00 - 2024-09-11 20:00:00
Shapes=> Dates: 108251, TEC: (108251, 72, 72), OMNI: (108251, 17)
Data Split Sets: ['train_v1', 'test_v1', 'train_v2', 'valid_v1', 'train_v3', 'test_v2', 'train_v4', 'valid_v2', 'train_v5', 'test_v3', 'train_v6', 'valid_v3']
Storm Info: ['Intense', 'Superintense']
Max TEC: 210.100, Min TEC: 0.0
--------------------
Train: 74880, Valid: 16597, Test: 16344
Dataset Name: stratified 
 Ratio => Train: 0.69, Valid: 0.15, Test: 0.15


In [26]:
# 4a: Solar Analysis >>> Analysis Function (Testing on Solar intensity classes: very weak, weak, moderate, intense) (RUN TIME: >~20 Mins)
#====================================================================================
from source.myTrainFuns import SolarAnalysis

# FOR SOLAR ANALYSIS UNCOMMENT BELOW
#================================================================
'''
cfgs.session.name = "SimVPv2_test"  # Writes on top of the previous test file if the session name is the same.
cfgs.test.save_results = True       # Appends the test results to a log file (txt) that exists in the training_sessions folder under the session name. (if not exists, creates a new one) 
cfgs.test.save_raw = False          # Save the raw test results (Prediction Dates, TEC predictions and dedicated truth maps) to npz. (Per solar class)
solarDict = SolarAnalysis(model, data, loaders, device=device, cfg=cfgs).run()
'''
#====================================================================================

'\ncfgs.session.name = "SimVPv2_test"  # Writes on top of the previous test file if the session name is the same.\ncfgs.test.save_results = True       # Appends the test results to a log file (txt) that exists in the training_sessions folder under the session name. (if not exists, creates a new one) \ncfgs.test.save_raw = False          # Save the raw test results (Prediction Dates, TEC predictions and dedicated truth maps) to npz. (Per solar class)\nsolarDict = SolarAnalysis(model, data, loaders, device=device, cfg=cfgs).run()\n'

---
### 4b: Storm Analysis

In [28]:
# 4b: Storm Analysis >>> Storm Loaders
#====================================================================================
from scripts.data import make_storm_loaders

if "loaders" in locals():
    del loaders, data, cfgs             # To clear memory before loading solar loaders
    
import gc
gc.collect()
torch.cuda.empty_cache()

cfgs = load_configs(
                 model = "SimVPv2",  # <= change to "DCNN121", "SwinLSTM" for other models. (But the loaded model should match the model name)
                 mode = "storm",     # <= changed to storm to load storm configurations dynamically.
                 split = "stratified", 
                 base_path= base_path
                 )
cfgs.paths.base_dir = base_path
data = prepare_raw(cfgs)                # Prepare the data (again neeeded for setting important parameters to config inside) 
loaders = make_storm_loaders(cfg = cfgs, d = data)                # Make default loaders for training, validation, and test sets.
#====================================================================================

--------------------
Base Path: /usr1/home/s124mdg45_01/IonoBench
Function Path: /usr1/home/s124mdg45_01/IonoBench/source
Training Data Path: /usr1/home/s124mdg45_01/IonoBench/datasets
--------------------
Training data loaded successfully.
--------------------
Important Details:
Data Range: 2000-01-01 00:00:00 - 2024-09-11 20:00:00
Shapes=> Dates: 108251, TEC: (108251, 72, 72), OMNI: (108251, 17)
Data Split Sets: ['train_v1', 'test_v1', 'train_v2', 'valid_v1', 'train_v3', 'test_v2', 'train_v4', 'valid_v2', 'train_v5', 'test_v3', 'train_v6', 'valid_v3']
Storm Info: ['Intense', 'Superintense']
Max TEC: 210.100, Min TEC: 0.0
--------------------
Train: 74880, Valid: 16597, Test: 16344
Dataset Name: stratified 
 Ratio => Train: 0.69, Valid: 0.15, Test: 0.15
Preparing DataLoaders for storm analysis...
Found 16 storms intersecting with the test set.


In [49]:
# 4b: Storm Analysis >>> Analysis Function (Testing on Storm events) (RUN TIME: ~1-3 Mins)
#====================================================================================
from source.myTrainFuns import StormAnalysis

cfgs.test.save_results = True           # Save the test results to a log file (txt).
cfgs.test.save_raw = True               # Save the raw test results (Prediction Dates, TEC predictions and dedicated truth maps) to npz.
cfgs.session.name = "SimVPv2_test"      # Write a session name for the test results. New name will create a new folder in the ~/IonoBenchv1/training_sessions/
testDict = StormAnalysis(model, data, cfgs, loaders,device).run() 
#====================================================================================

Analyzing Storms: 100%|██████████| 16/16 [01:11<00:00,  4.47s/it, Date: 2012-11-14, Dst: -103.0 nT]


Storm analysis complete. Log appended to: /usr1/home/s124mdg45_01/IonoBench/training_sessions/SimVPv2_test/test_log_2025-07-13_11-45-55.txt
Raw storm data saved in: /usr1/home/s124mdg45_01/IonoBench/training_sessions/SimVPv2_test/storms


--- 
## 5: Storm Predictions and Residuals
---
  

In [ ]:
from IPython.display import HTML
from source.myVisualFuns import spatialComparison_Anim
cfgs.session.name = "SimVPv2_test"      # Write a session name for the test results. New name will create a new folder in the ~/IonoBenchv1/training_sessions/
# Example Storm Animation (Storm 2, 2001-11-06)
npz_path = base_path / "training_sessions" / cfgs.session.name / "storms" / "test_raw_storm_2_2001-11-06.npz"
'''  
Here you can observe the results of paper's section "5.3.3. Visual Comparison: Residual Patterns during Stormy vs. Quiet Conditions
This is the animation for whole main phase of the storm.
'''
anim = spatialComparison_Anim(
    npz_path=npz_path,
    dataDict=dataDict,
    cfgs=cfgs,
    n_start=33,             # Starting storm index (0-72, default 0) 33 is start of main phase +-6h
    n_end=40,               # Ending storm index (0-72, default None, uses all) 40 is end of main phase +-6h
    horizon=6,              # 0-11 steps: 0 → 2h, 5 → 12h, etc.
    interval_ms=300,
    save=True              # set False if you only want inline display
)

HTML(anim.to_jshtml())


Prepared 7 frames
Saving GIF → /usr1/home/s124mdg45_01/IonoBench/visuals/SimVPv2_test_14h_storm2_samples33-39.gif …
